In [5]:
import json
import sys
import random
import gc

sys.path.append("../")

from models.vector_model import vector_model
from tqdm import tqdm
from preprocessors.preprocessor import Preprocessor

import pandas as pd
import numpy as np

import IR_utils

random.seed(0)
np.random.seed(0)

%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [6]:
data_path = "../../data/dataset/corpus.jsonl"
docs = IR_utils.load_document_corpus(data_path=data_path, max_docs=500000)

print("Number of documents in corpus: {}".format(len(docs)))

preprocessor = Preprocessor()
tokenized_docs = preprocessor.preprocess(docs)

Number of documents in corpus: 500000


100%|██████████| 500000/500000 [02:48<00:00, 2973.03it/s]


In [7]:
vm = vector_model.create_model(documents=tokenized_docs, min_df=50)
vm

{'invent': 1288, 'cotton': 685, 'gin': 100, 'becam': 3584, 'americaâ\x80\x99': 286, 'lead': 7530, 'crop': 972, 'king': 2665, '1790': 96, 'america': 5067, 'produc': 11018, '1500': 1019, 'pound': 3356, '1800': 651, 'product': 15296, 'increas': 11071, '35000': 191, 'timer': 178, 'separ': 4437, 'night': 4327, 'day': 26681, 'outlet': 595, 'nice': 1277, 'time': 40013, 'set': 14457, 'rotat': 1344, '24': 4984, 'hr': 811, 'dial': 501, 'pin': 875, 'around': 14173, 'outer': 1349, 'perimet': 178, 'oper': 7999, 'one': 56675, 'rais': 3091, '12': 10471, 'hour': 14557, 'per': 16786, 'turn': 7525, 'rosebuy': 1, 'public': 7187, 'still': 8743, 'encount': 749, 'wide': 5906, 'varieti': 6022, 'price': 10243, 'anyth': 2705, '10': 16293, 'dozen': 601, 'red': 6368, 'rose': 1115, 'local': 7755, 'corner': 1498, 'store': 7079, '20': 9485, 'supermarket': 256, '90': 2876, 'highend': 167, 'florist': 57, 'map': 3439, 'wendov': 2, 'aut': 3, 'airport': 2273, 'detail': 5588, 'env': 5, 'present': 6862, 'may': 41735, 'use

In [8]:
vm.fit()
print(vm.describe())

Building TF-iDF Matrix: 500000item [00:22, 21921.36item/s]


: 

In [ ]:
train_queries, all_queries = IR_utils.load_train_queries(
    "../../data/dataset/queries.jsonl", "../../data/task1_train.tsv"
)

test_queries, all_queries = IR_utils.load_test_queries(
    "../../data/dataset/queries.jsonl", "../../data/task1_test.tsv"
)

In [ ]:
TOP_K = 10

query_ids = list(test_queries.keys())

for query_id in tqdm(query_ids):
    d2v_query_answers = vm.find_similar(test_queries[query_id]["text"], TOP_K)

    retrieved_doc_ids = [id for id, score in d2v_query_answers]
    retrieved_doc_scores = [score for id, score in d2v_query_answers]

    test_queries[query_id]["retrieved_doc_ids"] = retrieved_doc_ids
    test_queries[query_id]["retrieved_doc_scores"] = retrieved_doc_scores